In [ ]:
import pandas as pd
pd.set_option('display.max_columns', None)
import numpy as np
import re
from IPython.core.display import display, HTML
from bs4 import BeautifulSoup
import requests
import seaborn as sns
import matplotlib.pyplot as plt
import pickle
from collections import defaultdict 
import nltk
# nltk.download('punkt')
nltk.download('wordnet')
nltk.download('stopwords')
# nltk.download('maxent_ne_chunker')
# nltk.download('words')
import re
import string
from nltk.corpus import stopwords
from nltk.stem.lancaster import LancasterStemmer
from nltk.tokenize import RegexpTokenizer
from nltk.stem import WordNetLemmatizer
from nltk.tag import pos_tag
from nltk.chunk import ne_chunk
from sklearn.feature_extraction.text import CountVectorizer
from nltk.tokenize import word_tokenize
from sklearn.feature_extraction.text import TfidfVectorizer

In [326]:
with open('coffee_words.pickle','rb') as read_file:
    coffee = pickle.load(read_file)
with open('coffee_ratings.pickle','rb') as read_file:
    ratings = pickle.load(read_file)

In [3]:
coffee.head()

Roaster  \
0             Jackrabbit Java   
1             Jackrabbit Java   
2  Red Rooster Coffee Roaster   
3           Paradise Roasters   
4               Kakalove Cafe   

                                              Review  \
0  Yeasty, richly sweet-savory. Fresh-baked bread...   
1  Balanced, sweet-toned, floral. Tea rose, cocoa...   
2  Delicate, deep; complex. Pomegranate, macadami...   
3  Very sweet, floral-toned. Freesia, pink grapef...   
4  Opulent, richly sweet-tart-savory. Black curra...   

                                               Notes  \
0  Processed by the anaerobic natural method (who...   
1  Produced at Mahembe Farm and processed at the ...   
2  This coffee earned the highest rating in a cup...   
3  This coffee tied for the second-highest rating...   
4  This coffee tied for the second-highest rating...   

                                                TLDR  
0  An anaerobically processed coffee with rich st...  
1  A friendly, classic Rwanda cup: balanced, deep...  
2  An intricately original natural-processed Colo...  
3  A sweetly evocative presentation of Colombia P...  
4  A rich, complex, decadently sweet cup processe...

In [126]:
ratings = ratings.reset_index().rename(columns={'index':'Roaster'})
ratings.head()

Roaster Overall        Roaster Location  \
0             Jackrabbit Java      93    Thermopolis, Wyoming   
1             Jackrabbit Java      92    Thermopolis, Wyoming   
2  Red Rooster Coffee Roaster      96         Floyd, Virginia   
3           Paradise Roasters      95  Minneapolis, Minnesota   
4               Kakalove Cafe      95         Chia-Yi, Taiwan   

                                       Coffee Origin   Roast Level Agtron  \
0                                         Costa Rica  Medium-Light  54/72   
1                        Nyamasheke District, Rwanda  Medium-Light  58/76   
2  Los Naranjos, La Argentina, Huila Department, ...         Light  64/84   
3                                    Huila, Colombia         Light  62/80   
4                     Antioquia Department, Colombia  Medium-Light  60/80   

         Est. Price    Review Date Aroma Body Flavor Aftertaste Acidity  
0  $20.00/12 ounces  February 2021     9    9      9          8       8  
1  $20.00/12 ounces  February 2021     9    8      9          8       8  
2   $18.99/8 ounces  February 2021     9    9     10          9       9  
3   $16.95/6 ounces  February 2021     9    9      9          9       9  
4  NT $310/8 ounces  February 2021     9    9      9          9       9

## Combine the review, notes, and summary columns of the review into one note. Remove any websites and the common final sentence about phone numbers or visiting Facebook

In [319]:
df = pd.DataFrame()
df['Roaster'] = coffee['Roaster']
df['TextA'] = coffee.Review + coffee.Notes + coffee.TLDR
# for ind in range(len(df)):   
# df['TextA'] = re.sub('[^ ]+\.[^ ]+','',df.Total.str)
# df['TextB'] = re.sub(r'Visit.*\n?','',df.TextA.str)
df['TextB'] = df.TextA.str.replace('[^ ]+\.[^ ]+','',regex=True)
df['Text'] = df.TextB.str.replace(r'Visit.*\n?','',regex=True)
df.drop(columns=['TextA','TextB'],inplace=True)

with open('df_full.pickle', 'wb') as to_write:
    pickle.dump(df, to_write)
    
df.head()

Roaster  \
0             Jackrabbit Java   
1             Jackrabbit Java   
2  Red Rooster Coffee Roaster   
3           Paradise Roasters   
4               Kakalove Cafe   

                                                Text  
0  Yeasty, richly sweet-savory. Fresh-baked bread...  
1  Balanced, sweet-toned, floral. Tea rose, cocoa...  
2  Delicate, deep; complex. Pomegranate, macadami...  
3  Very sweet, floral-toned. Freesia, pink grapef...  
4  Opulent, richly sweet-tart-savory. Black curra...

In [317]:
df.Text[3232]

'Gracefully intense aromatics with suggestions of lemon blossom, tart plum and apple round into a sweet-toned cup: honey, lemon, stone fruit. Tartly bright acidity; dry but lightly syrupy mouthfeel; long floral and lemony  sample consists entirely of peaberries, a kind of bean that results when the coffee fruit develops only a single, oval bean rather than the usual pair of flat-sided beans. Peaberries produce a somewhat different (often better) cup than normal beans from the same crop, from which they may or may not be separated during grading. JBC Coffee Roasters (formerly Johnson Brothers Coffee Roasters) is a distinguished small-batch roasting company. '

## CountVectorizer and TF-IDF

In [320]:
from nltk.corpus import stopwords
sw = stopwords.words("english")
sw = sw + ['coffee','coffees','cup','john', 'diruocco','jen','apodaca','ken','kevin','keurig','espresso','serve','capsule','device','serving','flavor','notes','mouthfeel','aroma','finish','brewed','brewing','parts','one','two','three','evaluate','evaluated','hint']

In [321]:
# Create count vectorizer on all reviews not counting rare words/misspellings or extremely common, such as "coffee"
vectorizer = CountVectorizer(min_df=10, stop_words = sw)
doc_word = vectorizer.fit_transform(df.Text.str.replace(r'\d+','',regex=True))

# Create a similar count vectorizer, but only on the shorter summaries (TLDR)
tldrvectorizer = CountVectorizer(min_df=10, stop_words = sw)
tldr_word = tldrvectorizer.fit_transform(coffee.TLDR.str.replace(r'\d+','',regex=True))

In [322]:
# Create TF-IDF matrix for full corpus from website
fulltfidf = TfidfVectorizer(min_df=10, stop_words = sw)
tfidf_full = fulltfidf.fit_transform(df.Text.str.replace(r'\d+','',regex=True))

In [323]:
# Create count vectorizer on the blind tasting notes portion of the reviews
blindvectorizer = CountVectorizer(min_df=10, stop_words = sw)
blind_word = blindvectorizer.fit_transform(coffee.Review.str.replace(r'\d+','',regex=True))

# Create TF-IDF matrix on the blind tasting notes portion of the reviews
blindtfidf = TfidfVectorizer(min_df=10, stop_words = sw)
tfidf_blind = blindtfidf.fit_transform(coffee.Review.str.replace(r'\d+','',regex=True))

In [337]:
pd.DataFrame(blindvectorizer.transform(['hello red fruit berry acidic strong black']).toarray()).sum(axis=1)[0]

5

In [341]:
user_input = 'Very sweet, floral-toned. Freesia, pink grapefruit zest, wild honey, guava, oak in aroma and cup. Balanced, richly sweet structure with high-toned acidity; viscous, satiny mouthfeel. The flavor-saturated finish centers around notes of freesia and pink grapefruit zest.'
user_text = [user_input]
word_count = pd.DataFrame()
word_count['text'] = user_text
word_count['length'] = word_count.text.str.replace(r'\d+','',regex=True).str.len()
word_count['word count'] = pd.DataFrame(blindvectorizer.transform(user_text).toarray()).sum(axis=1)[0]
word_count.drop(columns='text',inplace=True)
word_count

length  word count
0     268          27

In [327]:
with open('blindtfidf_vec.pickle', 'wb') as to_write:
    pickle.dump(blindtfidf, to_write)
with open('blindtfidf_mat.pickle', 'wb') as to_write:
    pickle.dump(tfidf_blind, to_write)
with open('blindvectorizer.pickle', 'wb') as to_write:
    pickle.dump(blindvectorizer, to_write)

## Work for stemming/lemmatizing

In [10]:
def preprocess_textstem(text):
    # Remove numbers
    text = re.sub(r'\d+', '', text)
    
    # Tokenise words while ignoring punctuation
    tokeniser = RegexpTokenizer(r'\w+')
    tokens = tokeniser.tokenize(text)
    
     # Lowercase and stem
    stemmer = LancasterStemmer()
    stems = [stemmer.stem(token.lower()) for token in tokens]
    
    # Remove stopwords
    keywords= [stem for stem in stems if stem not in stopwords.words('english')]
    return keywords

In [12]:
def preprocess_textlemma(text):
    # Remove numbers
    text = re.sub(r'\d+', '', text)
    
    # Tokenise words while ignoring punctuation
    tokeniser = RegexpTokenizer(r'\w+')
    tokens = tokeniser.tokenize(text)
    
    # Lowercase and lemmatise 
    lemmatiser = WordNetLemmatizer()
    lemmas = [lemmatiser.lemmatize(token.lower(), pos='v') for token in tokens]
    
    # Remove stopwords
    keywords= [lemma for lemma in lemmas if lemma not in stopwords.words('english')]
    return keywords

In [16]:
# Create an instance of TfidfVectorizer
sample_vector = TfidfVectorizer(analyzer=preprocess_textlemma)
# Fit to the data and transform to feature matrix
sample_lemma = sample_vector.fit_transform(df.Text.head())
# Convert sparse matrix to dataframe
sample_lemma = pd.DataFrame.sparse.from_spmatrix(sample_lemma)
# Save mapping on which index refers to which words
col_map = {v:k for k, v in sample_vector.vocabulary_.items()}
# Rename each column using the mapping
for col in sample_lemma.columns:
    sample_lemma.rename(columns={col: col_map[col]}, inplace=True)
sample_lemma

achicue   acidity     add   agave       air  alliance    almond  \
0  0.000000  0.000000  0.0000  0.0000  0.113155  0.000000  0.000000   
1  0.000000  0.078101  0.0000  0.0000  0.111844  0.000000  0.277256   
2  0.000000  0.071212  0.1264  0.1264  0.000000  0.000000  0.000000   
3  0.122191  0.068840  0.0000  0.0000  0.000000  0.000000  0.000000   
4  0.000000  0.068777  0.0000  0.0000  0.000000  0.122078  0.000000   

   anaerobic   arabica     aroma    around      asia      bake   balance  \
0   0.113155  0.000000  0.066831  0.093929  0.000000  0.420757  0.000000   
1   0.000000  0.000000  0.066057  0.092841  0.000000  0.000000  0.185681   
2   0.000000  0.084652  0.120461  0.000000  0.000000  0.000000  0.000000   
3   0.000000  0.163665  0.058225  0.081833  0.122191  0.000000  0.081833   
4   0.098492  0.081757  0.058171  0.000000  0.000000  0.000000  0.081757   

      batch     black   blossom   bourbon     bread      café     candy  \
0  0.000000  0.000000  0.000000  0.000000  0.140252  0.000000  0.140252   
1  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000   
2  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000   
3  0.122191  0.000000  0.000000  0.122191  0.000000  0.000000  0.000000   
4  0.000000  0.122078  0.122078  0.000000  0.000000  0.122078  0.000000   

    caturra    caucho     cedar    center   certify    cherry      chia  \
0  0.000000  0.000000  0.113155  0.000000  0.000000  0.000000  0.000000   
1  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000  0.000000   
2  0.101979  0.000000  0.000000  0.000000  0.101979  0.000000  0.000000   
3  0.000000  0.122191  0.000000  0.122191  0.000000  0.000000  0.000000   
4  0.098492  0.000000  0.098492  0.000000  0.098492  0.122078  0.122078   

   chocolate  chocolaty  cinnamon      city     cocoa    coffee   coffees  \
0   0.226309   0.000000  0.280504  0.000000  0.000000  0.000000  0.133662   
1   0.000000   0.000000  0.000000  0.000000  0.138628  0.000000  0.132114   
2   0.000000   0.000000  0.000000  0.000000  0.000000  0.253955  0.060230   
3   0.000000   0.000000  0.000000  0.000000  0.000000  0.163665  0.174674   
4   0.098492   0.122078  0.000000  0.122078  0.000000  0.327028  0.058171   

   colombia   company  complex  conscious  consolidate     craft       cup  \
0  0.000000  0.000000   0.0000     0.0000     0.140252  0.000000  0.066831   
1  0.000000  0.000000   0.0000     0.0000     0.000000  0.000000  0.066057   
2  0.169303  0.000000   0.1264     0.1264     0.000000  0.000000  0.180691   
3  0.081833  0.122191   0.0000     0.0000     0.000000  0.122191  0.116449   
4  0.163514  0.000000   0.0000     0.0000     0.000000  0.000000  0.116342   

    currant       cut      dark    deep    deeply  delicate    dill       dry  \
0  0.000000  0.140252  0.000000  0.0000  0.000000    0.0000  0.0000  0.066831   
1  0.000000  0.000000  0.000000  0.0000  0.000000    0.0000  0.0000  0.066057   
2  0.000000  0.000000  0.000000  0.1264  0.000000    0.1264  0.1264  0.060230   
3  0.000000  0.000000  0.000000  0.0000  0.000000    0.0000  0.0000  0.058225   
4  0.122078  0.000000  0.122078  0.0000  0.122078    0.0000  0.0000  0.058171   

     earn        el   elegant    emerge  entirely  establish      farm  \
0  0.0000  0.000000  0.000000  0.000000  0.000000     0.0000  0.000000   
1  0.0000  0.000000  0.000000  0.000000  0.000000     0.0000  0.078101   
2  0.1264  0.000000  0.000000  0.000000  0.000000     0.1264  0.071212   
3  0.0000  0.122191  0.000000  0.122191  0.098583     0.0000  0.068840   
4  0.0000  0.000000  0.122078  0.000000  0.098492     0.0000  0.068777   

   february  fermentation     finca    finest    finish    flavor     flesh  \
0  0.000000      0.113155  0.000000  0.093929  0.079016  0.000000  0.000000   
1  0.000000      0.000000  0.000000  0.092841  0.078101  0.000000  0.111844   
2  0.084652      0.000000  0.000000  0.000000  0.071212  0.101979  0.000000   
3  0.081833      0.000000  0.098583  0

In [18]:
# Create an instance of TfidfVectorizer
vectorizer = TfidfVectorizer(analyzer=preprocess_textlemma)
# Fit to the data and transform to feature matrix
lemmas = vectorizer.fit_transform(df.Text)
# Convert sparse matrix to dataframe
lemmas = pd.DataFrame.sparse.from_spmatrix(lemmas)
# Save mapping on which index refers to which words
col_map = {v:k for k, v in vectorizer.vocabulary_.items()}
# Rename each column using the mapping
for col in lemmas.columns:
    lemmas.rename(columns={col: col_map[col]}, inplace=True)
lemmas

aa  aaa  aaanyone  aaseattle  aayou   ab  ababa  abad  abafita  \
0     0.0  0.0       0.0        0.0    0.0  0.0    0.0   0.0      0.0   
1     0.0  0.0       0.0        0.0    0.0  0.0    0.0   0.0      0.0   
2     0.0  0.0       0.0        0.0    0.0  0.0    0.0   0.0      0.0   
3     0.0  0.0       0.0        0.0    0.0  0.0    0.0   0.0      0.0   
4     0.0  0.0       0.0        0.0    0.0  0.0    0.0   0.0      0.0   
...   ...  ...       ...        ...    ...  ...    ...   ...      ...   
5954  0.0  0.0       0.0        0.0    0.0  0.0    0.0   0.0      0.0   
5955  0.0  0.0       0.0        0.0    0.0  0.0    0.0   0.0      0.0   
5956  0.0  0.0       0.0        0.0    0.0  0.0    0.0   0.0      0.0   
5957  0.0  0.0       0.0        0.0    0.0  0.0    0.0   0.0      0.0   
5958  0.0  0.0       0.0        0.0    0.0  0.0    0.0   0.0      0.0   

      abakundakawa  abandon  abaryoshyakawa  abay  abbey  abbreviation  \
0              0.0      0.0             0.0   0.0    0.0           0.0   
1              0.0      0.0             0.0   0.0    0.0           0.0   
2              0.0      0.0             0.0   0.0    0.0           0.0   
3              0.0      0.0             0.0   0.0    0.0           0.0   
4              0.0      0.0             0.0   0.0    0.0           0.0   
...            ...      ...             ...   ...    ...           ...   
5954           0.0      0.0             0.0   0.0    0.0           0.0   
5955           0.0      0.0             0.0   0.0    0.0           0.0   
5956           0.0      0.0             0.0   0.0    0.0           0.0   
5957           0.0      0.0             0.0   0.0    0.0           0.0   
5958           0.0      0.0             0.0   0.0    0.0           0.0   

      abdullah  aberdare  abet  ability  able  abregado  abril  abroad  \
0          0.0       0.0   0.0      0.0   0.0       0.0    0.0     0.0   
1          0.0       0.0   0.0      0.0   0.0       0.0    0.0     0.0   
2          0.0       0.0   0.0      0.0   0.0       0.0    0.0     0.0   
3          0.0       0.0   0.0      0.0   0.0       0.0    0.0     0.0   
4          0.0       0.0   0.0      0.0   0.0       0.0    0.0     0.0   
...        ...       ...   ...      ...   ...       ...    ...     ...   
5954       0.0       0.0   0.0      0.0   0.0       0.0    0.0     0.0   
5955       0.0       0.0   0.0      0.0   0.0       0.0    0.0     0.0   
5956       0.0       0.0   0.0      0.0   0.0       0.0    0.0     0.0   
5957       0.0       0.0   0.0      0.0   0.0       0.0    0.0     0.0   
5958       0.0       0.0   0.0      0.0   0.0       0.0    0.0     0.0   

      abruptly  absence  absent  absolute  absolutely  absorb  absorbingly  \
0          0.0      0.0     0.0       0.0         0.0     0.0          0.0   
1          0.0      0.0     0.0       0.0         0.0     0.0          0.0   
2          0.0      0.0     0.0       0.0         0.0     0.0          0.0   
3          0.0      0.0     0.0       0.0         0.0     0.0          0.0   
4          0.0      0.0     0.0       0.0         0.0     0.0          0.0   
...        ...      ...     ...       ...         ...     ...          ...   
5954       0.0      0.0     0.0       0.0         0.0     0.0          0.0   
5955       0.0      0.0     0.0       0.0         0.0     0.0          0.0   
5956       0.0      0.0     0.0       0.0         0.0     0.0          0.0   
5957       0.0      0.0     0.0       0.0         0.0     0.0          0.0   
5958       0.0      0.0     0.0       0.0         0.0     0.0          0.0   

      abstract  abstractly  abu  abundancia  abundant  abundantly  abuse  \
0          0.0         0.0  0.0         0.0       0.0         0.0    0.0   
1          0.0         0.0  0.0         0.0       0.0         0.0    0.0   
2          0.0         0.0  0.0         0.0       0.0         0.0    0.0   
3          0.0         0.0  0.0         0.0       0.0         0.0    0.0   
4          0.0         0.0  0.0    

In [19]:
with open('corpus_lemmas.pickle', 'wb') as to_write:
    pickle.dump(lemmas, to_write)

In [20]:
lemmas.shape

(5959, 11026)

In [ ]:
with open('reviews_stemmed.pickle', 'wb') as to_write:
    pickle.dump(stem_X, to_write)

In [ ]:
with open('reviews_lemma.pickle', 'wb') as to_write:
    pickle.dump(lemma_X, to_write)

In [ ]:
with open('reviews_stemmed.pickle','rb') as read_file:
    reviews_stemmed = pickle.load(read_file)

In [ ]:
with open('reviews_lemma.pickle','rb') as read_file:
    reviews_lemma = pickle.load(read_file)

<5959x478 sparse matrix of type '<class 'numpy.int64'>'
	with 48512 stored elements in Compressed Sparse Row format>